In [1]:
import pandas as pd
import os

from helpers import (
    get_combined_df,
    save_final_df_as_jsonl,
    handle_slug_column_mappings,
)

In [2]:
DATA_DIR = "../data"
PROCESSED_DIR = "../processed/"
FACET_DIR = "sales/"
FULL_DATA_DIR_PATH = os.path.join(DATA_DIR, FACET_DIR)
FULL_PROCESSED_DIR_PATH = os.path.join(PROCESSED_DIR, FACET_DIR)

In [3]:
exclude_columns = [
    "RegionID",
    "SizeRank",
    "RegionName",
    "RegionType",
    "StateName",
    "Home Type",
]

slug_column_mappings = {
    "_median_sale_to_list_": "Median Sale to List Ratio",
    "_mean_sale_to_list_": "Mean Sale to List Ratio",
    "_median_sale_price_": "Median Sale Price",
    "_pct_sold_above_list_": "% Sold Above List",
    "_pct_sold_below_list_": "% Sold Below List",
    "_sales_count_now_": "Nowcast",
}

data_frames = []

for filename in os.listdir(FULL_DATA_DIR_PATH):
    if filename.endswith(".csv"):
        print("processing " + filename)
        # ignore monthly data for now since it is redundant
        if "month" in filename:
            continue

        cur_df = pd.read_csv(os.path.join(FULL_DATA_DIR_PATH, filename))

        if "_sfrcondo_" in filename:
            cur_df["Home Type"] = "all homes"
        elif "_sfr_" in filename:
            cur_df["Home Type"] = "SFR"

        data_frames = handle_slug_column_mappings(
            data_frames, slug_column_mappings, exclude_columns, filename, cur_df
        )


combined_df = get_combined_df(
    data_frames,
    [
        "RegionID",
        "SizeRank",
        "RegionName",
        "RegionType",
        "StateName",
        "Home Type",
        "Date",
    ],
)

combined_df

processing Metro_mean_sale_to_list_uc_sfrcondo_sm_month.csv
processing Metro_median_sale_to_list_uc_sfrcondo_week.csv
processing Metro_median_sale_price_uc_sfr_week.csv
processing Metro_pct_sold_below_list_uc_sfrcondo_sm_month.csv
processing Metro_median_sale_price_uc_sfr_sm_sa_week.csv
processing Metro_pct_sold_below_list_uc_sfrcondo_month.csv
processing Metro_median_sale_price_uc_sfrcondo_sm_week.csv
processing Metro_pct_sold_below_list_uc_sfrcondo_sm_week.csv
processing Metro_median_sale_price_uc_sfr_month.csv
processing Metro_median_sale_to_list_uc_sfrcondo_sm_month.csv
processing Metro_pct_sold_above_list_uc_sfrcondo_month.csv
processing Metro_median_sale_to_list_uc_sfrcondo_sm_week.csv
processing Metro_median_sale_price_uc_sfrcondo_sm_sa_month.csv
processing Metro_sales_count_now_uc_sfrcondo_month.csv
processing Metro_pct_sold_above_list_uc_sfrcondo_week.csv
processing Metro_mean_sale_to_list_uc_sfrcondo_sm_week.csv
processing Metro_median_sale_price_uc_sfrcondo_sm_month.csv
proc

RegionID  SizeRank           RegionName RegionType StateName  \
0         102001         0        United States    country       NaN   
1         102001         0        United States    country       NaN   
2         102001         0        United States    country       NaN   
3         102001         0        United States    country       NaN   
4         102001         0        United States    country       NaN   
...          ...       ...                  ...        ...       ...   
255019    845160       198  Prescott Valley, AZ        msa        AZ   
255020    845160       198  Prescott Valley, AZ        msa        AZ   
255021    845160       198  Prescott Valley, AZ        msa        AZ   
255022    845160       198  Prescott Valley, AZ        msa        AZ   
255023    845160       198  Prescott Valley, AZ        msa        AZ   

        Home Type        Date  Median Sale to List Ratio  Median Sale Price  \
0             SFR  2008-02-02                        NaN           172000.0   
1             SFR  2008-02-09                        NaN           165400.0   
2             SFR  2008-02-16                        NaN           168000.0   
3             SFR  2008-02-23                        NaN           167600.0   
4             SFR  2008-03-01                        NaN           168100.0   
...           ...         ...                        ...                ...   
255019  all homes  2023-11-11                   0.985132           515000.0   
255020  all homes  2023-11-18                   0.972559           510000.0   
255021  all homes  2023-11-25                   0.979644           484500.0   
255022  all homes  2023-12-02                   0.978261           538000.0   
255023  all homes  2023-12-09                   0.981498           485000.0   

        Median Sale Price (Smoothed) (Seasonally Adjusted)  \
0                                                     NaN    
1                                                     NaN    
2                                                     NaN    
3                                                     NaN    
4                                                     NaN    
...                                                   ...    
255019                                           480020.0    
255020                                           476901.0    
255021                                           496540.0    
255022                                           510491.0    
255023                                           503423.0    

        Median Sale Price (Smoothed)  % Sold Below List (Smoothed)  \
0                                NaN                           NaN   
1                                NaN                           NaN   
2                                NaN                           NaN   
3                           167600.0                           NaN   
4                           168100.0                           NaN   
...                              ...                           ...   
255019                      480020.0                      0.651221   
255020                      476901.0                      0.659583   
255021                      496540.0                      0.669387   
255022                      510491.0                      0.678777   
255023                      503423.0                      0.658777   

        Median Sale to List Ratio (Smoothed)  % Sold Above List  \
0                                        NaN                NaN   
1                                        NaN                NaN   
2                                        NaN                NaN   
3                                        NaN                NaN   
4                                        NaN                NaN   
...                                      ...                ...   
255019                              0.982460           0.080000   
255020                              0.980362           0.142857   
25502

In [6]:
# Adjust column names
final_df = combined_df.rename(
    columns={
        "RegionID": "Region ID",
        "SizeRank": "Size Rank",
        "RegionName": "Region",
        "RegionType": "Region Type",
        "StateName": "State",
    }
)

final_df["Date"] = pd.to_datetime(final_df["Date"])
final_df.sort_values(by=["Region ID", "Home Type", "Date"])

Region ID  Size Rank               Region Region Type State  \
0          102001          0        United States     country   NaN   
1          102001          0        United States     country   NaN   
2          102001          0        United States     country   NaN   
3          102001          0        United States     country   NaN   
4          102001          0        United States     country   NaN   
...           ...        ...                  ...         ...   ...   
255019     845160        198  Prescott Valley, AZ         msa    AZ   
255020     845160        198  Prescott Valley, AZ         msa    AZ   
255021     845160        198  Prescott Valley, AZ         msa    AZ   
255022     845160        198  Prescott Valley, AZ         msa    AZ   
255023     845160        198  Prescott Valley, AZ         msa    AZ   

        Home Type       Date  Median Sale to List Ratio  Median Sale Price  \
0             SFR 2008-02-02                        NaN           172000.0   
1             SFR 2008-02-09                        NaN           165400.0   
2             SFR 2008-02-16                        NaN           168000.0   
3             SFR 2008-02-23                        NaN           167600.0   
4             SFR 2008-03-01                        NaN           168100.0   
...           ...        ...                        ...                ...   
255019  all homes 2023-11-11                   0.985132           515000.0   
255020  all homes 2023-11-18                   0.972559           510000.0   
255021  all homes 2023-11-25                   0.979644           484500.0   
255022  all homes 2023-12-02                   0.978261           538000.0   
255023  all homes 2023-12-09                   0.981498           485000.0   

        Median Sale Price (Smoothed) (Seasonally Adjusted)  \
0                                                     NaN    
1                                                     NaN    
2                                                     NaN    
3                                                     NaN    
4                                                     NaN    
...                                                   ...    
255019                                           480020.0    
255020                                           476901.0    
255021                                           496540.0    
255022                                           510491.0    
255023                                           503423.0    

        Median Sale Price (Smoothed)  % Sold Below List (Smoothed)  \
0                                NaN                           NaN   
1                                NaN                           NaN   
2                                NaN                           NaN   
3                           167600.0                           NaN   
4                           168100.0                           NaN   
...                              ...                           ...   
255019                      480020.0                      0.651221   
255020                      476901.0                      0.659583   
255021                      496540.0                      0.669387   
255022                      510491.0                      0.678777   
255023                      503423.0                      0.658777   

        Median Sale to List Ratio (Smoothed)  % Sold Above List  \
0                                        NaN                NaN   
1                                        NaN                NaN   
2                                        NaN                NaN   
3                                        NaN                NaN   
4                                        NaN                NaN   
...                                      ...                ...   
255019                              0.982460           0.080000   
255020                              0.980362           0.142857   
255021                       

In [7]:
save_final_df_as_jsonl(FULL_PROCESSED_DIR_PATH, final_df)